In [1]:
import numpy as np
from sklearn.datasets import fetch_20newsgroups
from nltk.tokenize import RegexpTokenizer
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from keras.layers.embeddings import Embedding
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score
from sklearn.svm import LinearSVC
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
import string
import keras
import nltk
import os

In [2]:
nltk.download("stopwords")
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [3]:
nltk_stopw = stopwords.words('english')

In [4]:
!wget http://nlp.stanford.edu/data/glove.6B.zip
!unzip -q glove.6B.zip

--2021-05-05 14:01:58--  http://nlp.stanford.edu/data/glove.6B.zip
Resolving nlp.stanford.edu (nlp.stanford.edu)... 171.64.67.140
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:80... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://nlp.stanford.edu/data/glove.6B.zip [following]
--2021-05-05 14:01:58--  https://nlp.stanford.edu/data/glove.6B.zip
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: http://downloads.cs.stanford.edu/nlp/data/glove.6B.zip [following]
--2021-05-05 14:01:59--  http://downloads.cs.stanford.edu/nlp/data/glove.6B.zip
Resolving downloads.cs.stanford.edu (downloads.cs.stanford.edu)... 171.64.64.22
Connecting to downloads.cs.stanford.edu (downloads.cs.stanford.edu)|171.64.64.22|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 862182613 (822M) [application/zip]
Saving to: ‘glove.6B.zip’

glove.6

In [5]:
!wget https://dl.fbaipublicfiles.com/fasttext/vectors-english/crawl-300d-2M-subword.zip
!unzip -q crawl-300d-2M-subword.zip

--2021-05-05 14:05:09--  https://dl.fbaipublicfiles.com/fasttext/vectors-english/crawl-300d-2M-subword.zip
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 172.67.9.4, 104.22.75.142, 104.22.74.142, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|172.67.9.4|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 5828358084 (5.4G) [application/zip]
Saving to: ‘crawl-300d-2M-subword.zip’

crawl-300d-2M-subwo 100%[===================>]   5.43G  10.8MB/s    in 10m 33s 

2021-05-05 14:15:43 (8.78 MB/s) - ‘crawl-300d-2M-subword.zip’ saved [5828358084/5828358084]



In [6]:
!wget https://dl.fbaipublicfiles.com/fasttext/vectors-english/crawl-300d-2M.vec.zip
!unzip -q crawl-300d-2M.vec.zip

--2021-05-05 14:17:43--  https://dl.fbaipublicfiles.com/fasttext/vectors-english/crawl-300d-2M.vec.zip
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 104.22.75.142, 172.67.9.4, 104.22.74.142, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|104.22.75.142|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1523785255 (1.4G) [application/zip]
Saving to: ‘crawl-300d-2M.vec.zip’

crawl-300d-2M.vec.z 100%[===================>]   1.42G  13.9MB/s    in 1m 51s  

2021-05-05 14:19:35 (13.1 MB/s) - ‘crawl-300d-2M.vec.zip’ saved [1523785255/1523785255]



In [7]:
!wget http://nlp.stanford.edu/data/glove.840B.300d.zip
!unzip -q glove.840B.300d.zip

--2021-05-05 14:20:21--  http://nlp.stanford.edu/data/glove.840B.300d.zip
Resolving nlp.stanford.edu (nlp.stanford.edu)... 171.64.67.140
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:80... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://nlp.stanford.edu/data/glove.840B.300d.zip [following]
--2021-05-05 14:20:22--  https://nlp.stanford.edu/data/glove.840B.300d.zip
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: http://downloads.cs.stanford.edu/nlp/data/glove.840B.300d.zip [following]
--2021-05-05 14:20:22--  http://downloads.cs.stanford.edu/nlp/data/glove.840B.300d.zip
Resolving downloads.cs.stanford.edu (downloads.cs.stanford.edu)... 171.64.64.22
Connecting to downloads.cs.stanford.edu (downloads.cs.stanford.edu)|171.64.64.22|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2176768927 (2.0G) [application/zip

# **MIMIC-III Dataset**

In [8]:
import pandas as pd
from sklearn.model_selection import train_test_split

df = pd.read_csv('drive/MyDrive/ai_project/more_data.csv')
X = df['Text'].values
y = df['Expire_label'].values

In [9]:
# Remove punc, stopwords, numbers
filtered_X = []
num_remove, total = 0, 0
for s in X:
    tokenizer = RegexpTokenizer(r"\w+")
    s = tokenizer.tokenize(s)
    total += len(s)
    filtered_w = [w.strip().lower() for w in s if w.strip().lower() not in nltk_stopw]
    num_remove += (len(s) - len(filtered_w))
    filtered_s = " ".join(filtered_w)
    filtered_X.append(filtered_s)

print('Total number of words: ', total)
print('Total number of stopwords: ', num_remove)

Total number of words:  26602560
Total number of stopwords:  6056586


In [10]:
# One example
print(X[1])
print(filtered_X[1])

Addendum to NPN
Baby had 1 [**Name2 (NI) **] with apnea & desat while feeding that required mild stim.

addendum npn baby 1 name2 ni apnea desat feeding required mild stim


In [11]:
# Split the filtered data
train_val_data, test_data, train_val_label, test_label = train_test_split(filtered_X, y, test_size=0.30, random_state=42)

In [12]:
# Extract a training & validation split
validation_split = 0.2
num_validation_samples = int(validation_split * len(train_val_data))
train_data = train_val_data[:-num_validation_samples]
val_data = train_val_data[-num_validation_samples:]
train_label = train_val_label[:-num_validation_samples]
val_label = train_val_label[-num_validation_samples:]

In [13]:
print(len(train_data), len(val_data), len(test_data))

56000 14000 30000


In [14]:
print(len(train_label), len(val_label), len(test_label))

56000 14000 30000


# **Create Embedding Matrix**

In [15]:
# Turn text into 200-long integer sequences
# padding with 0 if necessary to maintain the length at 200
# Only pick Top 20,000 words

sequenceLength = 200
kTokenizer = keras.preprocessing.text.Tokenizer(num_words=20000)
kTokenizer.fit_on_texts(train_val_data)

encoded_docs = kTokenizer.texts_to_sequences(train_data)
X_train_seq = keras.preprocessing.sequence.pad_sequences(encoded_docs, maxlen=sequenceLength, padding='post')

encoded_docs = kTokenizer.texts_to_sequences(val_data)
X_val_seq = keras.preprocessing.sequence.pad_sequences(encoded_docs, maxlen=sequenceLength, padding='post')

encoded_docs = kTokenizer.texts_to_sequences(test_data)
X_test_seq = keras.preprocessing.sequence.pad_sequences(encoded_docs, maxlen=sequenceLength, padding='post')

In [16]:
# Show top-10 words
import json
word_count = kTokenizer.get_config()['word_counts']
word_count = json.loads(word_count)
word_count_sorted = dict(sorted(word_count.items(), key=lambda x: x[1], reverse=True)[:10])
word_count_sorted

{'1': 158393,
 '2': 149007,
 '3': 106707,
 '4': 93331,
 '5': 92230,
 '7': 71704,
 '8': 68216,
 'left': 73385,
 'name': 68644,
 'pt': 102621}

In [17]:
# Choose the embedding method
embedding_file = ['crawl-300d-2M.vec', 'crawl-300d-2M-subword.vec', 'glove.6B.300d.txt', 'glove.840B.300d.txt', 'none'][3]

if embedding_file != 'none':
    embeddings_index = {}
    with open(embedding_file) as f:
        for line in f:
            word, coefs = line.split(maxsplit=1)
            coefs = np.fromstring(coefs, "f", sep=" ")
            embeddings_index[word] = coefs

    print("Found %s word vectors." % len(embeddings_index))

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: DeprecationWarning: string or file could not be read to its end due to unmatched data; this will raise a ValueError in the future.
  if __name__ == '__main__':


Found 2195884 word vectors.


In [18]:
word_index = kTokenizer.word_index
num_tokens = len(kTokenizer.word_index) + 1

embedding_dim = 300
hits = 0
misses = 0

# Prepare embedding matrix
embedding_matrix = np.zeros((num_tokens, embedding_dim))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None and len(embedding_vector) == embedding_dim:
        # Words not found in embedding index will be all-zeros.
        # This includes the representation for "padding" and "OOV"
        embedding_matrix[i] = embedding_vector
        hits += 1
    else:
        misses += 1
        # print(word)
print("Converted %d words (%d misses)" % (hits, misses))

Converted 59789 words (52613 misses)


In [19]:
print(embedding_matrix.shape)

(112403, 300)


# **Bag of Words + SVM**

In [35]:
# Bag of words representation
count_vect = CountVectorizer()
X_train_bow = count_vect.fit_transform(train_data)
X_test_bow = count_vect.transform(test_data)
print(X_train_bow.shape, X_test_bow.shape)

(56000, 73405) (30000, 73405)


In [36]:
y_train, y_test, y_val = train_label, test_label, val_label

In [38]:
# Hyperparameter search
from sklearn.model_selection import GridSearchCV

max_iter_range = [10, 100, 1000, 10000]
c_range = [0.01, 0.1, 1, 10, 100, 1000]
param_grid = dict(C=c_range, max_iter=max_iter_range)

linear_svc =  LinearSVC(tol=1e-5)

grid = GridSearchCV(linear_svc, param_grid, cv=5, scoring='accuracy')
grid.fit(X_train_bow, y_train)

print(grid.best_score_)
print(grid.best_params_)

/usr/local/lib/python3.7/dist-packages/sklearn/svm/_base.py:947: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


0.7286428571428571
{'C': 0.01, 'max_iter': 100}


In [39]:
# Train and Predict with Linear SVM
model = LinearSVC(tol=1e-5, C=0.01, max_iter=100)
model.fit(X_train_bow, y_train)
y_pred = model.predict(X_test_bow)

/usr/local/lib/python3.7/dist-packages/sklearn/svm/_base.py:947: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [40]:
acc = accuracy_score(y_test, y_pred)
prec = precision_score(y_test, y_pred)
recall = recall_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

print(acc, prec, recall, f1)

0.7334333333333334 0.6872802812400128 0.6781237682301932 0.6826713225665648


# **TF-IDF + SVM**

In [41]:
# TF-IDF representation
tf_transformer = TfidfTransformer(use_idf=True).fit(X_train_bow)
X_train_tf = tf_transformer.transform(X_train_bow)
X_test_tf = tf_transformer.transform(X_test_bow)
print(X_train_tf.shape, X_test_tf.shape)

(56000, 73405) (30000, 73405)


In [42]:
# Hyperparameter search

max_iter_range = [10, 100, 1000, 10000]
c_range = [0.01, 0.1, 1, 10, 100, 1000]
param_grid = dict(C=c_range, max_iter=max_iter_range)

linear_svc =  LinearSVC(tol=1e-5)

grid = GridSearchCV(linear_svc, param_grid, cv=5, scoring='accuracy')
grid.fit(X_train_tf, y_train)

print(grid.best_score_)
print(grid.best_params_)

/usr/local/lib/python3.7/dist-packages/sklearn/svm/_base.py:947: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


0.7397142857142858
{'C': 0.1, 'max_iter': 100}


In [43]:
# Train and Predict with Linear SVM
model = LinearSVC(tol=1e-5, C=0.1, max_iter=100)
model.fit(X_train_tf, y_train)
y_pred = model.predict(X_test_tf)

In [44]:
acc = accuracy_score(y_test, y_pred)
prec = precision_score(y_test, y_pred)
recall = recall_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

print(acc, prec, recall, f1)

0.7445333333333334 0.6942660372978411 0.7072920772566023 0.7007185254607935


# **Word Embedding + LSTM**

In [59]:
# LSTM model
model = keras.models.Sequential()
if (embedding_file != 'none'):
    embedding = Embedding(input_dim=num_tokens, output_dim=300, weights=[embedding_matrix], 
                          input_length=sequenceLength, trainable=False, mask_zero=True)
else:
    embedding = Embedding(input_dim=num_tokens, output_dim=300, 
                          input_length=sequenceLength, trainable=True, mask_zero=True)
    
model.add(embedding)
model.add(keras.layers.LSTM(units=128, dropout=0.2, recurrent_dropout=0.2, return_sequences=True))
model.add(keras.layers.LSTM(units=128, dropout=0.2, recurrent_dropout=0.2, return_sequences=False))
model.add(keras.layers.Dense(1, activation='sigmoid'))
opt = keras.optimizers.Adam(learning_rate=0.001)
model.compile(optimizer=opt, loss='binary_crossentropy', metrics=['acc'])
model.summary()

Model: "sequential_4"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_4 (Embedding)      (None, 200, 300)          33720900  
_________________________________________________________________
lstm_8 (LSTM)                (None, 200, 128)          219648    
_________________________________________________________________
lstm_9 (LSTM)                (None, 128)               131584    
_________________________________________________________________
dense_4 (Dense)              (None, 1)                 129       
Total params: 34,072,261
Trainable params: 351,361
Non-trainable params: 33,720,900
_________________________________________________________________


In [60]:
# Train and predict with LSTM
y_train = train_label
y_test = test_label
y_val = val_label

early_stop = keras.callbacks.EarlyStopping(monitor='val_loss', min_delta=0, patience=5, verbose=1, 
                                           mode='auto', restore_best_weights=False)
history = model.fit(X_train_seq, y_train, epochs=20, batch_size=32, 
                    shuffle=True, validation_data = (X_val_seq, y_val), 
                    callbacks=[early_stop], verbose=1)

Epoch 1/20
1750/1750 [==============================] - 2091s 1s/step - loss: 0.6134 - acc: 0.5987 - val_loss: 0.5571 - val_acc: 0.6581
Epoch 2/20
1750/1750 [==============================] - 2089s 1s/step - loss: 0.5495 - acc: 0.6764 - val_loss: 0.5315 - val_acc: 0.7036
Epoch 3/20
1750/1750 [==============================] - 2093s 1s/step - loss: 0.5195 - acc: 0.7149 - val_loss: 0.5150 - val_acc: 0.7183
Epoch 4/20
1750/1750 [==============================] - 2090s 1s/step - loss: 0.5025 - acc: 0.7314 - val_loss: 0.4994 - val_acc: 0.7304
Epoch 5/20
1750/1750 [==============================] - 2095s 1s/step - loss: 0.4855 - acc: 0.7439 - val_loss: 0.4999 - val_acc: 0.7344
Epoch 6/20
1750/1750 [==============================] - 2089s 1s/step - loss: 0.4682 - acc: 0.7558 - val_loss: 0.5060 - val_acc: 0.7336
Epoch 7/20
1750/1750 [==============================] - 2097s 1s/step - loss: 0.4527 - acc: 0.7697 - val_loss: 0.5084 - val_acc: 0.7341
Epoch 8/20
1750/1750 [==========================

In [63]:
predicted = model.predict(X_test_seq, verbose=0)
y_pred = predicted > 0.5
y_pred = y_pred.astype('int32')

In [64]:
acc = accuracy_score(y_test, y_pred)
prec = precision_score(y_test, y_pred)
recall = recall_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

print(acc, prec, recall, f1)

0.7345 0.6669968864987263 0.7430823807646827 0.702986911287616


# **Word Embeddiing + BiLSTM**

In [65]:
# BiLSTM model
model = keras.models.Sequential()
if (embedding_file != 'none'):
    embedding = Embedding(input_dim=num_tokens, output_dim=300, weights=[embedding_matrix], 
                          input_length=sequenceLength, trainable=False, mask_zero=True)
else:
    embedding = Embedding(input_dim=num_tokens, output_dim=300, 
                          input_length=sequenceLength, trainable=True, mask_zero=True)
model.add(embedding)
model.add(keras.layers.Bidirectional(keras.layers.LSTM(128, dropout=0.2, recurrent_dropout=0.2, return_sequences=True)))
model.add(keras.layers.Bidirectional(keras.layers.LSTM(128, dropout=0.2, recurrent_dropout=0.2)))
model.add(keras.layers.Dense(1, activation='sigmoid'))
opt = keras.optimizers.Adam(learning_rate=0.001)
model.compile(optimizer=opt, loss='binary_crossentropy', metrics=['acc'])

In [66]:
# Train and predict with BiLSTM

y_train = train_label
y_test = test_label
y_val = val_label

early_stop = keras.callbacks.EarlyStopping(monitor='val_loss', min_delta=0, patience=5, verbose=1, 
                                           mode='auto', restore_best_weights=False)
history = model.fit(X_train_seq, y_train, epochs=20, batch_size=32, 
                    shuffle=True, validation_data = (X_val_seq, y_val), 
                    callbacks=[early_stop], verbose=1)

Epoch 1/20
1750/1750 [==============================] - 4676s 3s/step - loss: 0.5927 - acc: 0.6347 - val_loss: 0.5500 - val_acc: 0.6754
Epoch 2/20
1750/1750 [==============================] - 4694s 3s/step - loss: 0.5462 - acc: 0.6850 - val_loss: 0.5172 - val_acc: 0.7152
Epoch 3/20
1750/1750 [==============================] - 4703s 3s/step - loss: 0.5146 - acc: 0.7163 - val_loss: 0.5070 - val_acc: 0.7260
Epoch 4/20
1750/1750 [==============================] - 4711s 3s/step - loss: 0.5006 - acc: 0.7305 - val_loss: 0.5103 - val_acc: 0.7211
Epoch 5/20
1750/1750 [==============================] - 4728s 3s/step - loss: 0.4793 - acc: 0.7483 - val_loss: 0.5018 - val_acc: 0.7246
Epoch 6/20
1750/1750 [==============================] - 4767s 3s/step - loss: 0.4593 - acc: 0.7627 - val_loss: 0.5045 - val_acc: 0.7327
Epoch 7/20
1750/1750 [==============================] - 4786s 3s/step - loss: 0.4406 - acc: 0.7791 - val_loss: 0.5079 - val_acc: 0.7395
Epoch 8/20
1750/1750 [==========================

In [67]:
predicted = model.predict(X_test_seq, verbose=0)
y_pred = predicted > 0.5
y_pred = y_pred.astype('int32')

In [68]:
acc = accuracy_score(test_label, y_pred)
prec = precision_score(test_label, y_pred)
recall = recall_score(test_label, y_pred)
f1 = f1_score(test_label, y_pred)

print(acc, prec, recall, f1)

0.7279666666666667 0.6682534959833383 0.7082380764682696 0.6876650465000573


# **Self-attention Model**

In [20]:
!pip install keras-self-attention
!pip install keras-multi-head

  Created wheel for keras-self-attention: filename=keras_self_attention-0.49.0-cp37-none-any.whl size=19468 sha256=fc7173b29a5b3d57c6a363d58cf478d06b105dd4a4bd1ef964844b4ad0270407
  Stored in directory: /root/.cache/pip/wheels/6f/9d/c5/26693a5092d9313daeae94db04818fc0a2b7a48ea381989f34
Successfully built keras-self-attention
  Created wheel for keras-multi-head: filename=keras_multi_head-0.27.0-cp37-none-any.whl size=15611 sha256=e1c55b01585cff44d36c38b1bb1788c559b4dd97bd5385d3337be5ac890da120
  Stored in directory: /root/.cache/pip/wheels/b5/b4/49/0a0c27dcb93c13af02fea254ff51d1a43a924dd4e5b7a7164d
  Created wheel for keras-self-attention: filename=keras_self_attention-0.46.0-cp37-none-any.whl size=17278 sha256=42cbebec3f9499c136a3517be755c180340d31d0d1e78b23278468a77c207643
  Stored in directory: /root/.cache/pip/wheels/d2/2e/80/fec4c05eb23c8e13b790e26d207d6e0ffe8013fad8c6bdd4d2
Successfully built keras-multi-head keras-self-attention
  Found existing installation: keras-self-attentio

In [21]:
from keras_self_attention import SeqSelfAttention

# Self-attention model
model = keras.models.Sequential()

if (embedding_file != 'none'):
    embedding = Embedding(input_dim=num_tokens, output_dim=300, weights=[embedding_matrix], 
                          input_length=sequenceLength, trainable=False, mask_zero=True)
else:
    embedding = Embedding(input_dim=num_tokens, output_dim=300, 
                          input_length=sequenceLength, trainable=True, mask_zero=True)
    
model.add(embedding)
model.add(keras.layers.LSTM(units=128, dropout=0.2, recurrent_dropout=0.2, return_sequences=True))
model.add(keras.layers.LSTM(units=128, dropout=0.2, recurrent_dropout=0.2, return_sequences=True))

model.add(SeqSelfAttention(attention_width=15, attention_activation='sigmoid'))

# Add DNN layers, and create Model.
model.add(keras.layers.Flatten())
model.add(keras.layers.Dense(1, activation='sigmoid'))
opt = keras.optimizers.Adam(learning_rate=0.001)
model.compile(optimizer=opt, loss='binary_crossentropy', metrics=['acc'])
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 200, 300)          33720900  
_________________________________________________________________
lstm (LSTM)                  (None, 200, 128)          219648    
_________________________________________________________________
lstm_1 (LSTM)                (None, 200, 128)          131584    
_________________________________________________________________
seq_self_attention (SeqSelfA (None, 200, 128)          8257      
_________________________________________________________________
flatten (Flatten)            (None, 25600)             0         
_________________________________________________________________
dense (Dense)                (None, 1)                 25601     
Total params: 34,105,990
Trainable params: 385,090
Non-trainable params: 33,720,900
______________________________________

In [ ]:
# Train and predict with LSTM
y_train = train_label
y_test = test_label
y_val = val_label

early_stop = keras.callbacks.EarlyStopping(monitor='val_loss', min_delta=0, patience=5, verbose=1, 
                                           mode='auto', restore_best_weights=False)
history = model.fit(X_train_seq, y_train, epochs=20, batch_size=32, 
                    shuffle=True, validation_data = (X_val_seq, y_val), 
                    callbacks=[early_stop], verbose=1)

Epoch 1/20
 703/1750 [===========>..................] - ETA: 27:11 - loss: 0.5984 - acc: 0.6290

In [ ]:
predicted = model.predict(X_test_seq, verbose=0)
y_pred = predicted > 0.5
y_pred = y_pred.astype('int32')

In [ ]:
acc = accuracy_score(test_label, y_pred)
prec = precision_score(test_label, y_pred)
recall = recall_score(test_label, y_pred)
f1 = f1_score(test_label, y_pred)

print(acc, prec, recall, f1)

# **Multi-Head attention**

In [ ]:
from keras_multi_head import MultiHead


# Self-attention model
model = keras.models.Sequential()

if (embedding_file != 'none'):
    embedding = Embedding(input_dim=num_tokens, output_dim=300, weights=[embedding_matrix], 
                          input_length=sequenceLength, trainable=False, mask_zero=True)
else:
    embedding = Embedding(input_dim=num_tokens, output_dim=300, 
                          input_length=sequenceLength, trainable=True, mask_zero=True)
    
model.add(embedding)

model.add(MultiHead([
    keras.layers.LSTM(units=128, dropout=0.2, recurrent_dropout=0.2, return_sequences=True),
    keras.layers.LSTM(units=128, dropout=0.2, recurrent_dropout=0.2, return_sequences=False)
], name='Multi-LSTMs'))

# Add DNN layers, and create Model.
model.add(keras.layers.Flatten())
model.add(keras.layers.Dense(1, activation='sigmoid'))
opt = keras.optimizers.Adam(learning_rate=0.001)
model.compile(optimizer=opt, loss='binary_crossentropy', metrics=['acc'])
model.summary()

In [ ]:
# Train and predict with LSTM

y_train = train_label
y_test = test_label
y_val = val_label

early_stop = keras.callbacks.EarlyStopping(monitor='val_loss', min_delta=0, patience=5, verbose=1, 
                                           mode='auto', restore_best_weights=False)
history = model.fit(X_train_seq, y_train, epochs=20, batch_size=32, 
                    shuffle=True, validation_data = (X_val_seq, y_val), 
                    callbacks=[early_stop], verbose=1)

In [ ]:
predicted = model.predict(X_test_seq, verbose=0)
y_pred = predicted > 0.5
y_pred = y_pred.astype('int32')

In [ ]:
acc = accuracy_score(test_label, y_pred)
prec = precision_score(test_label, y_pred)
recall = recall_score(test_label, y_pred)
f1 = f1_score(test_label, y_pred)

print(acc, prec, recall, f1)

# **Attention Layer Visualization**

In [27]:
# Choose how many examples for visualization (only show positive ground-truth)
num = 10
tp = np.where((test_label == 1) & (y_pred == 1))[0]
idx = tp[:num]
print(idx)

[ 0  2  4 17 19 23 25 28 35 36]


In [28]:
print('Ground truth label: ', test_label[idx])

print('Predicted label: ', y_pred[idx])

Ground truth label:  [1 1 1 1 1 1 1 1 1 1]
Predicted label:  [1 1 1 1 1 1 1 1 1 1]


In [29]:
all_weights = []

for i in idx:
    layer_weights = model.layers[3].get_weights()
    new_model = keras.Model(inputs=model.input, outputs=model.layers[2].output)
    output_before_att = new_model.predict(X_test_seq[i,:]) 
    eij = np.tanh(np.dot(output_before_att, layer_weights[0]) + layer_weights[1]) 
    eij = np.dot(eij, layer_weights[2]) 
    eij = eij.reshape((eij.shape[0], eij.shape[1])) 
    ai = np.exp(eij) 
    weights = ai / np.sum(ai) 
    all_weights.append(weights)

In [30]:
all_color_arrays = []
for i in range(num):
    color_array = np.mean(all_weights[i], axis=1)[:len(test_data[idx[i]].split(' '))] 
    color_array_norm = (color_array - np.min(color_array)) / (np.max(color_array) - np.min(color_array))
    all_color_arrays.append(color_array_norm)

In [31]:
import matplotlib
from IPython.display import display, HTML
def colorize(words, color_array):
    # words is a list of words
    # color_array is an array of numbers between 0 and 1 of length equal to words
    cmap = matplotlib.cm.Blues
    template = '<span class="barcode"; style="color: black; background-color: {}">{}</span>'
    colored_string = ''
    for word, color in zip(words, color_array):
        color = matplotlib.colors.rgb2hex(cmap(color)[:3])
        colored_string += template.format(color, '&nbsp' + word + '&nbsp')
    return colored_string

In [32]:
# Attention weights: darker blue means higher importance score
for i in range(num):
    print('Sample: ', idx[i])
    s = colorize(test_data[idx[i]].split(' '), all_color_arrays[i])
    display(HTML(s))

Sample:  0


Sample:  2


Sample:  4


Sample:  17


Sample:  19


Sample:  23


Sample:  25


Sample:  28


Sample:  35


Sample:  36
